In [107]:
import pandas as pd
import plotly.offline as pyo
pyo.init_notebook_mode()

In [178]:
MAPBOX = 'abc'
SEVERITY_LOOKUP = {'Fatal' : 'red',
                    'Serious' : 'orange',
                    'Slight' : 'yellow'}
SEX_LOOKUP = {'Female' : 'yellow',
              'Male' : 'blue'}
SLIGHT_FRAC = 0.1
SERIOUS_FRAC = 0.5
DAYSORT = dict(zip(['Friday', 'Monday', 'Saturday','Sunday', 'Thursday', 'Tuesday', 'Wednesday'],
                  [4, 0, 5, 6, 3, 1, 2]))

In [140]:
acc = pd.read_csv('accidents2017.csv', index_col = 0).dropna(how='any', axis = 0)
veh = pd.read_csv('vehicles2017.csv', index_col = 0).dropna(how='any', axis = 0)
cas = pd.read_csv('castualties2017.csv', index_col = 0).dropna(how='any', axis = 0)

In [13]:
def updateMapBox(severity):
    acc2 = acc[acc['Accident_Severity'].isin(severity)]

    traces = []

    # too many data points for the map to handle. Downsampling to around 10k points max in each category
    for sev in sorted(severity, reverse=True):
        sample = 1
        if sev == 'Slight':
            sample = SLIGHT_FRAC
        elif sev == 'Serious':
            sample = SERIOUS_FRAC
            
        acc2 = acc[acc['Accident_Severity'].isin(severity)].sample(frac=sample)
            
        # This trace holds the data
        traces.append({
            'type' : 'scattermapbox',
            'mode' : 'markers',
            'lat' : acc2['Latitude'][acc2['Accident_Severity'] == sev],
            'lon' : acc2['Longitude'][acc2['Accident_Severity'] == sev],
            'marker' : {
                'color' : SEVERITY_LOOKUP[sev],
                'size' : 2,
            
            },
            'name' : sev,
            'legendgroup' : sev,
            'showlegend' : False,
            'text' : acc2['Local_Authority_(District)'][acc2['Accident_Severity'] == sev]
        })
        
        # This trace is only for the legend items
        traces.append({
            'type' : 'scattermapbox',
            'mode' : 'markers',
            'lat' : [0],
            'lon' : [0],
            'marker' : {
                'color' : SEVERITY_LOOKUP[sev],
                'size' : 10,
            
            },
            'name' : sev,
            'legendgroup' : sev,
            
        })
    layout = {
        'height' : 900,
        'width' : 600,
        'paper_bgcolor' : 'rgb(26,25,25)', # To match the background colour of the map
        'autosize' : True,
        'hovermode' : 'closest',
        'mapbox' : {
            'accesstoken' : MAPBOX,
            #Probably have to change these in the production version
            'center' : {
                'lat' : 54.5,
                'lon' : -2
            },
            'zoom' : 5,
            'style' : 'dark',   
        },
        'margin' : {'t' : 0,
                   'b' : 0,
                   'l' : 0,
                   'r' : 0},
        'legend' : {  # Want to put the legend at the top
            'font' : {'color' : 'white'},
             'orientation' : 'h',
             'x' : 0,
             'y' : 1.01
        }
    }
    fig = dict(data=traces, layout=layout)
    return fig



pyo.iplot(updateMapBox(['Slight', 'Serious', 'Fatal']))

In [169]:
def updateBarChart(severity):
    acc_veh2 = pd.DataFrame(acc_veh[['Accident_Severity','Age_of_Driver','Number_of_Casualties']])
    acc_veh2 = acc_veh2.loc[acc_veh2['Age_of_Driver'] != -1]
    acc_veh2['Driver_Age_Group'] = acc_veh2['Age_of_Driver'].apply(lambda x: '{}0 ~ {}9'.format(str(x)[0], str(x)[0]))
    acc_veh2 = acc_veh2.drop(columns=['Age_of_Driver'])
    acc_veh2 = acc_veh2.groupby(['Accident_Severity','Driver_Age_Group']).sum().reset_index()

    traces = []
    for sev in severity:
        traces.append({
            'type' : 'bar',
            'x' : acc_veh2['Driver_Age_Group'][acc_veh2['Accident_Severity'] == sev],
            'y' : acc_veh2['Number_of_Casualties'][acc_veh2['Accident_Severity'] == sev],
            'marker' : {
                'color' : SEVERITY_LOOKUP[sev],
            'line' : {'width' : 2}},
            'orientation' : 'v',
            'name' : sev,
        })
        
    layout = {
        'title' : 'Accident Casualty and Severity by Driver Age',
        'xaxis' : {
            'title' : 'Driver Age Group'
        },
        'yaxis' : {
            'title' : 'Total Casualty'
        }
    }
        
    fig = {'data' : traces,
          'layout' : layout}
                    
    
    return fig

pyo.iplot(updateBarChart(['Slight', 'Serious', 'Fatal']))

In [179]:
def updateBarChart2(sex):
    cas2 = cas[['Sex_of_Casualty','Car_Passenger','Casualty_Type']].dropna()
    cas2 = cas2.loc[cas2['Sex_of_Casualty'].isin(['Female','Male'])]
    cas2 = cas2.loc[cas2['Casualty_Type'].isin(['Car occupant',
                                                'Bus or coach occupant (17 or more pass seats)',
                                                'Pedestrian',
                                                'Cyclist',
                                                'Motorcycle over 500cc rider or passenger',
                                                'Taxi/Private hire car occupant',
                                                'Van / Goods vehicle (3.5 tonnes mgw or under) occupant'])]
    cas2 = cas2.groupby(['Sex_of_Casualty','Casualty_Type']).count()
    cas2 = cas2.reset_index()
    
    traces = []
    for s in sex:
        traces.append({
            'type' : 'bar',
            'x' : cas2['Casualty_Type'][cas2['Sex_of_Casualty'] == s],
            'y' : cas2['Car_Passenger'][cas2['Sex_of_Casualty'] == s],
            'marker' : {
                'color' : SEX_LOOKUP[s],
            'line' : {'width' : 2}},
            'orientation' : 'v',
            'name' : s,
         })
        
    layout = {
        'title' : 'Casualty Count and Type by Sex',
        'xaxis' : {
            'title' : 'Casualty Type'
        },
        'yaxis' : {
            'title' : 'Total Casualty'
        }
    }
        
    fig = {'data' : traces,
          'layout' : layout}
                    
    
    return fig

pyo.iplot(updateBarChart2(['Female','Male']))

In [173]:
acc['Hour'] = acc['Time'].apply(lambda x: int(x[:2]))
acc.head()

Accident_Index  Longitude   Latitude  Number_of_Vehicles  \
0  2017010001708  -0.080107  51.650061                   2   
1  2017010017602  -0.078154  51.614239                   3   
2  2017010040017  -0.068296  51.635479                   2   
3  2017010042254  -0.085731  51.609237                   1   
4  2017010060597  -0.131287  51.688565                   3   

   Number_of_Casualties        Date   Time  Speed_limit         Police_Force  \
0                     3  05/08/2017  03:12           30  Metropolitan Police   
1                     1  11/02/2017  02:00           50  Metropolitan Police   
2                     1  27/05/2017  14:02           40  Metropolitan Police   
3                     1  10/06/2017  14:00           40  Metropolitan Police   
4                     2  23/09/2017  21:50           70  Metropolitan Police   

  Accident_Severity Day_of_Week Local_Authority_(District)  Hour  
0             Fatal    Saturday                    Enfield     3  
1             Fatal    Saturday                    Enfield     2  
2             Fatal    Saturday                    Enfield    14  
3             Fatal    Saturday                    Enfield    14  
4             Fatal    Saturday                    Enfield    21

In [175]:
def updateHeatmap(severity):
    acc2 = pd.DataFrame(acc[['Day_of_Week', 'Hour','Number_of_Casualties']][acc['Accident_Severity'].\
        isin(severity)].groupby(['Day_of_Week', 'Hour']).sum()).reset_index()
    
    z = []
    days = sorted(acc2['Day_of_Week'].unique(), key=lambda k: DAYSORT[k])
    hours = acc2['Hour'].unique()
    for d in days:
        row = acc2['Number_of_Casualties'][acc2['Day_of_Week'] == d].values.tolist()
        z.append(row)
    traces = [{
        'type' : 'heatmap',
        'x' : hours,
        'y' : days,
        'z' : z,
        'colorscale' : 'Jet'
    }]
    print(acc2.head())
        
    fig = {'data' : traces,
          'layout' : {}}
    return fig


pyo.iplot(updateHeatmap(['Slight', 'Serious', 'Fatal']))

  Day_of_Week  Hour  Number_of_Casualties
0      Friday     0                   329
1      Friday     1                   179
2      Friday     2                   158
3      Friday     3                   112
4      Friday     4                   115
